In [50]:
import json 
import os
import logging 
import concurrent 
import asyncio 
import re 
import requests 

from collections import deque 
from itertools import chain 
from datetime import date, datetime 

from typing import List 
from pprint import PrettyPrinter
from subgrounds import Subgrounds
from subgrounds.pagination import ShallowStrategy
from IPython.display import HTML, display
from web3 import Web3
from functools import partial 
from concurrent.futures import ThreadPoolExecutor
from gql import gql, Client
from gql.transport.aiohttp import AIOHTTPTransport

import pandas as pd 
import numpy as np 
import altair as alt 
import missingno as miss

# logging.basicConfig(level=logging.INFO)

# TODO: Figure out how this frax subgraph is useful
# https://api.thegraph.com/subgraphs/name/frax-finance-data/fraxbp-subgraph/graphql

pp = PrettyPrinter().pprint

alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [51]:
URL_INFURA = 'https://mainnet.infura.io/v3/856c3834f317452a82e25bb06e04de18'
w3 = Web3(Web3.HTTPProvider(URL_INFURA))

### Bribes Analysis 

We are interested in analyzing the impact of bribes through 

- Votium (voting power vlCVX, incentives in FXS) 
- Pitch 
- bribe.crv.finance 
- Hidden Hand 
- Aura 

that incentivize liquidity in liquidity pools that contain FRAX. To start, we are working with the following subset of pools that exist on curve. 
- Metapools (stable / non-stable). 
- Frax BP
- Frax:3crv

The following metrics are of interest

- \\$ Bribes spent per pool (broken down by platform and incentive type)  
- \\$ Liquidity per pool (broken into Frax and non-Frax components) 

Once we have both the liquidity and bribe information, we can try to answer these questions
- Where are bribe dollars best spent? 
- How does the Frax protocol optimize its bribing strategy in order to maximize the amount of liquidity within it's pools? 

In [52]:
def ddf(df):
    display(HTML(df.to_html()))
    
    
def remove_prefix(df: pd.DataFrame, prefix: str):
    # Remove a prefix from all columns 
    col_map = {}
    for i, c in enumerate(df.columns): 
        if c.startswith(prefix): 
            col_map[c] = c[len(prefix):]
    df = df.rename(columns=col_map) 
    return df 

def remove_prefixes(df: pd.DataFrame, prefixes: List[str]):
    for p in prefixes: 
        df = remove_prefix(df, p)
    return df 

def zip_dfs(dfs, col_names): 
    data = dfs[0]
    for i, c in enumerate(col_names): 
        data = data.merge(dfs[i+1][[c]], how='left', left_index=True, right_index=True)
    return data

def recursive_index_merge(dfs):
    drop_right_suffix = '__drop_right_suffix'
    assert all(len(dfs[0]) == len(dfs[i]) for i in range(1, len(dfs)))
    dfs = deque(dfs) 
    df = dfs.popleft()
    while dfs: 
        df_right = dfs.popleft()
        cols = list(set(df.columns).intersection(df_right.columns))
        df = df.merge(df_right, how='left', left_index=True, right_index=True, suffixes=(None, drop_right_suffix))
        drop_cols = [col for col in df.columns if col.endswith(drop_right_suffix)]
        df = df.drop(columns=drop_cols)
    return df 

def query_attrs(query, attrs):
    qattrs = []
    for a in attrs: 
        if '.' in a: 
            # nested
            v = None 
            for p in a.split('.'): 
                v = getattr(query, p) if v is None else getattr(v, p) 
            qattrs.append(v) 
        else: 
            # non-nested 
            qattrs.append(getattr(query, a)) 
    return sg.query_df(qattrs, pagination_strategy=ShallowStrategy) 

def camel_to_snake(name):
    name = re.sub('(.)([A-Z][a-z]+)', r'\1_\2', name)
    return re.sub('([a-z0-9])([A-Z])', r'\1_\2', name).lower()

def df_cols_camel_to_snake(df):
    col_map = {c: camel_to_snake(c) for c in df.columns}
    df = df.rename(columns=col_map) 
    return df 

def df_cols_change_prefix(df, prefix_cur, prefix_new):
    col_map = {}
    for c in df.columns: 
        if c.startswith(prefix_cur): 
            col_map[c] = prefix_new + c[len(prefix_cur):]
    df = df.rename(columns=col_map) 
    return df 

async def graphql_execute(
    query, 
    variable_values=None, 
    paginate=False, 
    page_size=10000, 
    page_size_variable='page_size', 
    page_offset_variable='page_offset',
    verbose=False, 
):
    variable_values = variable_values or {}
    transport = AIOHTTPTransport(url=URL_SNAPSHOT)
    # Using `async with` on the client will start a connection on the transport
    # and provide a `session` variable to execute queries on this connection
    async with Client(transport=transport, fetch_schema_from_transport=True) as session:
        if not paginate:
            gquery = gql(query)
            result = await session.execute(gquery)
            if verbose: 
                logging.info(f"Query returned {len(result)} records with page size {page_size}.")
            return result 
        else: 
            results = []
            finished = False 
            i = 0 
            while not finished:
                gquery = gql(query)
                # TODO: Could be a failure point but works for single queries 
                query_name = gquery.to_dict()['definitions'][0]['name']['value'].lower()
                query_resp = await session.execute(
                    gquery, variable_values={
                        **variable_values, page_offset_variable: page_size * i, page_size_variable: page_size
                    }
                )
                result = query_resp[query_name]
                if verbose: 
                    logging.info(f"Paginated query returned {len(result)} records with page size {page_size}.")
                finished = len(result) == 0
                results.append(result)
                i += 1
            return list(chain(*results)) 

In [92]:
# Non-subgraph
URL_SNAPSHOT = 'https://hub.snapshot.org/graphql'
# Subgraph 
URL_VOTIUM = 'https://api.thegraph.com/subgraphs/name/convex-community/votium-bribes' 
URL_CURVE_POOLS = 'https://api.thegraph.com/subgraphs/name/convex-community/curve-pools'
URL_CURVE_VOL_MAINNET = 'https://api.thegraph.com/subgraphs/name/convex-community/volume-mainnet' 
URL_CURVE_DAO = 'https://api.thegraph.com/subgraphs/name/convex-community/curve-dao'

# Addresses 
VOTIUM_VOTER = '0xde1E6A7ED0ad3F61D531a8a78E83CcDdbd6E0c49'.lower()
CURVE_POOL_FRAX_USDC = '0xdcef968d416a41cdac0ed8702fac8128a64241a2'
ADDRESS_FXS = '0x3432B6A60D23Ca0dFCa7761B7ab56459D9C964D0'.lower()
ADDRESS_CRVFRAX = '0x3175df0976dfa876431c2e9ee6bc45b65d3473cc'.lower()
ADDRESS_FRAXBP_POOL = '0xdcef968d416a41cdac0ed8702fac8128a64241a2'.lower()

In [93]:
# Instantiate the client with an endpoint.
sg = Subgrounds()

# votium_bribes = sg.load_subgraph(URL_VOTIUM) 
sg_curve_pools = sg.load_subgraph(URL_CURVE_POOLS) 
sg_curve_vol = sg.load_subgraph(URL_CURVE_VOL_MAINNET)
sg_votium = sg.load_subgraph(URL_VOTIUM) 
sg_curve_dao = sg.load_subgraph(URL_CURVE_DAO)

### Metapool TVL  

In [55]:
# Discovery of all curve metapools that have gauges 
# We will later get all pools paired with the fraxBP, and join in this extra gauge data for the relevant pools. 
query_metapools = sg_curve_pools.Query.pools(first=100, where={'coins_contains': [ADDRESS_CRVFRAX]})
attrs = [
    'id',
    'name',
    'gauge',
    'token', # convex receipt token. TODO: How does this work? 
    'lpToken', 
    'swap', # pool contract address 
    'coins',
    'assetType', 
]
df_metapools_gauges = query_attrs(query_metapools, attrs)
# df_metapools_gauges['pool_coin_index'] = df_metapools_gauges.groupby(['pools_id']).cumcount() + 1
df_metapools_gauges.pools_assetType = df_metapools_gauges.pools_assetType.apply(lambda v: {0: "STABLE", 4: "CRYPTO"}[int(v)])
df_metapools_gauges = df_cols_camel_to_snake(df_metapools_gauges) 
df_metapools_gauges = df_cols_change_prefix(df_metapools_gauges, "pools", "pool") 
assert len(df_metapools_gauges.pool_id.unique()) == len(df_metapools_gauges.pool_swap.unique()), "Detected duplicate metapools with gauges for FraxBP" 
df_metapools_gauges = df_metapools_gauges.rename(columns={
    'pool_token': 'pool_cvx_token',
    'pool_swap': 'pool_address',
    'pool_coins': 'pool_coin_address',
    'pool_asset_type': 'pool_type', 
}).drop(columns=['pool_id'])
df_metapools_gauges.head()

pool_name  \
0    Curve.fi Factory USD Metapool: sUSDFRAXBP   
1    Curve.fi Factory USD Metapool: sUSDFRAXBP   
2    Curve.fi Factory USD Metapool: LUSDFRAXBP   
3    Curve.fi Factory USD Metapool: LUSDFRAXBP   
4  Curve.fi Factory USD Metapool: apeUSDFRAXBP   

                                   pool_gauge  \
0  0xf6d7087d4ae4dcf85956d743406e63cda74d99ad   
1  0xf6d7087d4ae4dcf85956d743406e63cda74d99ad   
2  0x389fc079a15354e9cbce8258433cc0f85b755a42   
3  0x389fc079a15354e9cbce8258433cc0f85b755a42   
4  0xd6e48cc0597a1ee12a8beeb88e22bfdb81777164   

                               pool_cvx_token  \
0  0x8e2a6e9390cbd4c3895d07e4cb171c0527990df6   
1  0x8e2a6e9390cbd4c3895d07e4cb171c0527990df6   
2  0xe8a371b5d32344033589a2f0a2712dbd12130b18   
3  0xe8a371b5d32344033589a2f0a2712dbd12130b18   
4  0x5ec62bad0fa0c6b7f87b3b86edfe1bcd2a3139e2   

                                pool_lp_token  \
0  0xe3c190c57b5959ae62efe3b6797058b76ba2f5ef   
1  0xe3c190c57b5959ae62efe3b6797058b76ba2f5ef   
2  0x497ce58f34605b9944e6b15ecafe6b001206fd25   
3  0x497ce58f34605b9944e6b15ecafe6b001206fd25   
4  0x04b727c7e246ca70d496ecf52e6b6280f3c8077d   

                                 pool_address  \
0  0xe3c190c57b5959ae62efe3b6797058b76ba2f5ef   
1  0xe3c190c57b5959ae62efe3b6797058b76ba2f5ef   
2  0x497ce58f34605b9944e6b15ecafe6b001206fd25   
3  0x497ce58f34605b9944e6b15ecafe6b001206fd25   
4  0x04b727c7e246ca70d496ecf52e6b6280f3c8077d   

                            pool_coin_address pool_type  
0  0x57ab1ec28d129707052df4df418d58a2d46d5f51    STABLE  
1  0x3175df0976dfa876431c2e9ee6bc45b65d3473cc    STABLE  
2  0x5f98805a4e8be255a32880fdec7f6728c6568ba0    STABLE  
3  0x3175df0976dfa876431c2e9ee6bc45b65d3473cc    STABLE  
4  0xff709449528b6fb6b88f557f7d93dece33bca78d    STABLE

In [56]:
qattrs = [
    # pool attributes 
    'pool.id', 'pool.name', 'pool.lpToken', 'pool.symbol', 'pool.coins', 'pool.coinNames', 'pool.coinDecimals', 'pool.poolType', 'pool.metapool', 
    # snapshot attributes 
    'id', 'timestamp', 'reserves', 'reservesUSD', 'tvl', 'lpPriceUSD'
]
queries = [
    # FraxBP     
    sg_curve_vol.Query.dailyPoolSnapshots(first=100000, where={'pool': ADDRESS_FRAXBP_POOL}), 
    # FraxBP metapools 
    sg_curve_vol.Query.dailyPoolSnapshots(
        first=100000, 
        where={
            "pool_": {
                'coins_contains': [ADDRESS_CRVFRAX], 
                'cumulativeVolumeUSD_gt': 0, # There are some test pools and pools that were incorrectly created that we filter out by only getting pools with more than 0 volume 
                'id_not': '0xd3301b7caa76f932816a6fc7ef0b673238e217ad' # This is the BENTFRAXBP-f that was deprecated 
            }
        }
    )
]
dfs_concat = []
for q in queries: 
    dfs = query_attrs(q, qattrs) 
    df = recursive_index_merge(dfs)
    dfs_concat.append(df)
df_pool_snaps_raw = pd.concat(dfs_concat).sort_values(['dailyPoolSnapshots_id']).reset_index(drop=True)

In [57]:
print(len(df_pool_snaps_raw))
df_pool_snaps_raw.head()

5242


dailyPoolSnapshots_pool_id  \
0  0x02dfa5c793a9ce4d767a86259245a162a57f2db4   
1  0x02dfa5c793a9ce4d767a86259245a162a57f2db4   
2  0x02dfa5c793a9ce4d767a86259245a162a57f2db4   
3  0x02dfa5c793a9ce4d767a86259245a162a57f2db4   
4  0x02dfa5c793a9ce4d767a86259245a162a57f2db4   

                   dailyPoolSnapshots_pool_name  \
0  Curve.fi Factory Crypto Pool: bentCVX/FraxBP   
1  Curve.fi Factory Crypto Pool: bentCVX/FraxBP   
2  Curve.fi Factory Crypto Pool: bentCVX/FraxBP   
3  Curve.fi Factory Crypto Pool: bentCVX/FraxBP   
4  Curve.fi Factory Crypto Pool: bentCVX/FraxBP   

              dailyPoolSnapshots_pool_lpToken dailyPoolSnapshots_pool_symbol  \
0  0xbb23c0361d3e436fb7942a0e103edecab3afa917                   bentCVXFRX-f   
1  0xbb23c0361d3e436fb7942a0e103edecab3afa917                   bentCVXFRX-f   
2  0xbb23c0361d3e436fb7942a0e103edecab3afa917                   bentCVXFRX-f   
3  0xbb23c0361d3e436fb7942a0e103edecab3afa917                   bentCVXFRX-f   
4  0xbb23c0361d3e436fb7942a0e103edecab3afa917                   bentCVXFRX-f   

                dailyPoolSnapshots_pool_coins  \
0  0x9e0441e084f5db0606565737158aa6ab6b970fe0   
1  0x3175df0976dfa876431c2e9ee6bc45b65d3473cc   
2  0x9e0441e084f5db0606565737158aa6ab6b970fe0   
3  0x3175df0976dfa876431c2e9ee6bc45b65d3473cc   
4  0x9e0441e084f5db0606565737158aa6ab6b970fe0   

  dailyPoolSnapshots_pool_poolType  dailyPoolSnapshots_pool_metapool  \
0                   CRYPTO_FACTORY                             False   
1                   CRYPTO_FACTORY                             False   
2                   CRYPTO_FACTORY                             False   
3                   CRYPTO_FACTORY                             False   
4                   CRYPTO_FACTORY                             False   

                               dailyPoolSnapshots_id  \
0  0x02dfa5c793a9ce4d767a86259245a162a57f2db4-166...   
1  0x02dfa5c793a9ce4d767a86259245a162a57f2db4-166...   
2  0x02dfa5c793a9ce4d767a86259245a162a57f2db4-166...   
3  0x02dfa5c793a9ce4d767a86259245a162a57f2db4-166...   
4  0x02dfa5c793a9ce4d767a86259245a162a57f2db4-166...   

   dailyPoolSnapshots_timestamp  dailyPoolSnapshots_tvl  \
0                    1663113600                0.000000   
1                    1663113600                0.000000   
2                    1663200000              169.987405   
3                    1663200000              169.987405   
4                    1663286400              169.987856   

   dailyPoolSnapshots_lpPriceUSD dailyPoolSnapshots_pool_coinNames  \
0                       0.000000                           bentCVX   
1                       0.000000                           crvFRAX   
2                       2.280606                           bentCVX   
3                       2.280606                           crvFRAX   
4                       2.280612                           bentCVX   

   dailyPoolSnapshots_pool_coinDecimals dailyPoolSnapshots_reserves  \
0                                    18                           0   
1                                    18                           0   
2                                    18        32662705830000000000   
3                                    18       169869312990014343795   
4                                    18        32662705830000000000   

   dailyPoolSnapshots_reservesUSD  
0                        0.000000  
1                        0.000000  
2                        0.000000  
3                      169.987405  
4                        0.000000

In [58]:
def process(df): 
    """Get daily snapshots of tvl for all of the metapools. 
    """
    # Data processing and validation for pool snapshots 
    df = df_cols_change_prefix(df, "dailyPoolSnapshots_pool_", "pool_")
    df = df_cols_change_prefix(df, "dailyPoolSnapshots_", "snapshot_")
    df = df_cols_camel_to_snake(df)
    df = df.rename(columns={
        "pool_id": "pool_address", 
        "pool_pool_type": "pool_type", 
        "pool_coins": "pool_coin_address", 
        "pool_coin_names": "pool_coin_name", 
        "pool_coin_decimals": "pool_coin_decimals", 
    })
    df['pool_paired_fraxbp'] = df.pool_address != ADDRESS_FRAXBP_POOL
    df['snapshot_lp_supply'] = (df.snapshot_tvl / df.snapshot_lp_price_usd)
    df.pool_type = df.pool_type.apply(lambda v: v.replace("_FACTORY", ""))
    df.snapshot_timestamp = pd.to_datetime(df.snapshot_timestamp, unit='s')
    df = df.drop(columns=['snapshot_id']) 
    assert set(df.pool_type.unique()) == set(['STABLE', 'CRYPTO', 'REGISTRY_V1']), "Invalid pool type detected"
    assert len(df.pool_address.unique()) == len(df.pool_symbol.unique()), "Detected duplicate metapools for FraxBP" 
        
    # Join in gauge information
    merge_cols = ["pool_address", "pool_lp_token", "pool_coin_address"]
    df = df.merge(
        df_metapools_gauges[merge_cols + ['pool_gauge', 'pool_cvx_token']], 
        how='left', 
        on=merge_cols, 
        suffixes=(None, '_y')
    )
    gauge_mask = df.pool_address.isin(df_metapools_gauges.pool_address.unique().tolist()) 
    assert all(~df.loc[gauge_mask].isna())
    df['has_gauge'] = False 
    df.loc[gauge_mask, 'has_gauge'] = True 
        
    # Remove inactive pools
    last_snapshot = df.groupby(["pool_address", "pool_name"])['snapshot_reserves_usd'].last().reset_index()
    inactive_pools = last_snapshot.loc[last_snapshot.snapshot_reserves_usd < 1]
    if len(inactive_pools): 
        for p in inactive_pools.to_dict(orient="records"):
            peak_tvl = df.loc[df.pool_address == p['pool_address']]['snapshot_reserves_usd'].max()
            print(f"Removing data for inactive pool {p['pool_name']} with peak tvl {peak_tvl}.")
    inactive_addrs = inactive_pools.pool_address.unique()
    df = df.loc[~df.pool_address.isin(inactive_addrs)]
        
    # Processing after removing pools 
    assert not ((df.snapshot_tvl == 0) ^ (df.snapshot_lp_price_usd == 0)).any()
    df.snapshot_lp_supply = df.snapshot_lp_supply.fillna(0)
    # Add in column for total supply of crvFRAX over time 
    fraxbp_lp_supply = (
        df.loc[df.pool_address == ADDRESS_FRAXBP_POOL]
        [['snapshot_timestamp', 'snapshot_lp_supply']]
        .drop_duplicates()
        .rename(columns={'snapshot_lp_supply': 'snapshot_crvFRAX_supply'})
    )
    df = df.merge(fraxbp_lp_supply, how='left', on='snapshot_timestamp')
    assert not df.snapshot_crvFRAX_supply.isna().any()
    # Add in share of fraxbp that each metapool has 
    df_pool_bp_lp = (
        df.loc[(df.pool_address != ADDRESS_FRAXBP_POOL) & (df.pool_coin_name == 'crvFRAX')]
        [['pool_address', 'snapshot_timestamp', 'snapshot_reserves', 'pool_coin_decimals', 'snapshot_crvFRAX_supply']]
    )
    # number of lp tokens for base pool deposited in metapool 
    df_pool_bp_lp['snapshot_bp_lp_metapool'] = df_pool_bp_lp.snapshot_reserves / 10**df_pool_bp_lp.pool_coin_decimals 
    # fraction of number of lp tokens for base pool deposited in metapool to total supply of lp tokens in base pool 
    df_pool_bp_lp['snapshot_bp_lp_metapool_share'] = df_pool_bp_lp.snapshot_bp_lp_metapool / df_pool_bp_lp.snapshot_crvFRAX_supply
    # number of lp tokens for base pool desposited across all metapools 
    df_pool_bp_lp['snapshot_bp_lp_all_metapools'] = df_pool_bp_lp.groupby('snapshot_timestamp')['snapshot_bp_lp_metapool'].transform("sum")
    # fraction of number of lp tokens for base pool deposited in metapool to total number of lp tokens for base pool deposited across all metapools 
    df_pool_bp_lp['snapshot_bp_lp_all_metapools_share'] = 0
    mask = df_pool_bp_lp.snapshot_bp_lp_all_metapools != 0
    df_pool_bp_lp.loc[mask, 'snapshot_bp_lp_all_metapools_share'] = (
        df_pool_bp_lp.loc[mask, 'snapshot_bp_lp_metapool'] / df_pool_bp_lp.loc[mask, 'snapshot_bp_lp_all_metapools']
    )
    df = df.merge(
        df_pool_bp_lp[[
            'pool_address', 'snapshot_timestamp', 'snapshot_bp_lp_metapool', 'snapshot_bp_lp_metapool_share', 
            'snapshot_bp_lp_all_metapools', 'snapshot_bp_lp_all_metapools_share'
        ]], 
        how='left', on=['pool_address', 'snapshot_timestamp']
    )    
    assert set(df.loc[df.snapshot_bp_lp_metapool.isna()].pool_address.unique()) == set([ADDRESS_FRAXBP_POOL])
            
#     miss.matrix(df) 
#     miss.matrix(df.loc[df.pool_paired_fraxbp == True])
    
    return df 

df_pool_snaps = process(df_pool_snaps_raw.copy())
num_metapools = len(
    df_pool_snaps.loc[df_pool_snaps.pool_paired_fraxbp == True].pool_address.unique()
)
num_metapools_gauge = len(
    df_pool_snaps.loc[(df_pool_snaps.pool_paired_fraxbp == True) & (df_pool_snaps.has_gauge)].pool_address.unique()
)
print(f"Discovered {num_metapools} metapools.")
print(f"Number of pools with gauges: {num_metapools_gauge}")
assert len(df_pool_snaps.loc[df_pool_snaps.pool_paired_fraxbp == False].pool_address.unique()) == 1
ddf(df_pool_snaps.head(3))

Removing data for inactive pool Curve.fi Factory Crypto Pool: RAI/FRAXBP with peak tvl 22449.078786260372.
Discovered 23 metapools.
Number of pools with gauges: 18


In [59]:
df_bp_share = (
    df_pool_snaps.loc[(df_pool_snaps.pool_paired_fraxbp == True) & (df_pool_snaps.pool_coin_name == 'crvFRAX')]
    [['snapshot_timestamp', 'pool_symbol', 'snapshot_bp_lp_metapool', 'snapshot_bp_lp_metapool_share', 'snapshot_bp_lp_all_metapools', 'snapshot_bp_lp_all_metapools_share']]
)
df_bp_share_last = df_bp_share.loc[(
    (df_pool_snaps.pool_paired_fraxbp == True) & 
    (df_pool_snaps.pool_coin_name == 'crvFRAX') & 
    (df_bp_share.snapshot_timestamp == df_bp_share.snapshot_timestamp.max())
)]

In [60]:
# Table of most recent values 
# d = df_bp_share_last.copy()
# d.snapshot_bp_lp_metapool_share = d.snapshot_bp_lp_metapool_share * 100
# ddf(d.sort_values('snapshot_bp_lp_metapool_share', ascending=False).reset_index(drop=True))

chart_share_over_time = (
    alt.Chart(df_bp_share)
    .mark_area()
    .encode(
        x='snapshot_timestamp:T', 
        y=alt.Y('snapshot_bp_lp_metapool_share:Q', axis=alt.Axis(format=",%")), 
        color=alt.Color("pool_symbol:N", scale=alt.Scale(scheme="tableau20")), 
        tooltip=["pool_symbol:N", alt.Tooltip('snapshot_bp_lp_metapool_share:Q', format=",%")]
    )
) 
chart_current_share = (
    alt.Chart(df_bp_share_last)
    .mark_arc()
    .encode(
        theta='snapshot_bp_lp_metapool_share:Q', 
        color=alt.Color("pool_symbol:N", scale=alt.Scale(scheme="tableau20")), 
        tooltip=["pool_symbol:N", alt.Tooltip('snapshot_bp_lp_metapool_share:Q', format=",%")]
    )
)
chart_metapool_share = (
    alt.Chart(df_bp_share)
    .mark_area()
    .encode(
        x='snapshot_timestamp:T', 
        y=alt.Y('snapshot_bp_lp_all_metapools_share:Q', axis=alt.Axis(format=",%")), 
        color=alt.Color("pool_symbol:N", scale=alt.Scale(scheme="tableau20")), 
        tooltip=["pool_symbol:N", alt.Tooltip('snapshot_bp_lp_all_metapools_share:Q', format=",%")]
    )
)

chart_share_over_time | chart_current_share | chart_metapool_share

/opt/miniconda3/envs/frax-bribes/lib/python3.10/site-packages/altair/utils/core.py:317: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for col_name, dtype in df.dtypes.iteritems():


alt.HConcatChart(...)

### Metapool TVL Charts 

#### TVL Faceted by Metapool Segmented by Coin Name 

In [61]:
(
    alt.Chart(df_pool_snaps.loc[df_pool_snaps.pool_paired_fraxbp == True])
    .mark_area()
    .transform_calculate(stack_order="datum.pool_coin_name === 'crvFRAX' ? 0 : 1")
    .encode(
        x="snapshot_timestamp:T", 
        y="snapshot_reserves_usd:Q", 
        color=alt.Color("pool_coin_name:N", scale=alt.Scale(scheme="tableau20")), 
        tooltip=alt.Tooltip("snapshot_reserves_usd:Q", format='$,d'), 
        facet=alt.Facet('pool_name:N', columns=3),
        order="stack_order:O", 
    )
    .resolve_scale(y="independent")
    .resolve_axis(x="independent")
    .properties(width=250, height=150)
)
# TODO: Bent pool data is off for BENT tvl. 

alt.Chart(...)

#### Current Metapool Liquidity Faceted by Asset Type Segmented by Metapool

In [62]:
df_pool_snaps.head()

pool_address  \
0  0x02dfa5c793a9ce4d767a86259245a162a57f2db4   
1  0x02dfa5c793a9ce4d767a86259245a162a57f2db4   
2  0x02dfa5c793a9ce4d767a86259245a162a57f2db4   
3  0x02dfa5c793a9ce4d767a86259245a162a57f2db4   
4  0x02dfa5c793a9ce4d767a86259245a162a57f2db4   

                                      pool_name  \
0  Curve.fi Factory Crypto Pool: bentCVX/FraxBP   
1  Curve.fi Factory Crypto Pool: bentCVX/FraxBP   
2  Curve.fi Factory Crypto Pool: bentCVX/FraxBP   
3  Curve.fi Factory Crypto Pool: bentCVX/FraxBP   
4  Curve.fi Factory Crypto Pool: bentCVX/FraxBP   

                                pool_lp_token   pool_symbol  \
0  0xbb23c0361d3e436fb7942a0e103edecab3afa917  bentCVXFRX-f   
1  0xbb23c0361d3e436fb7942a0e103edecab3afa917  bentCVXFRX-f   
2  0xbb23c0361d3e436fb7942a0e103edecab3afa917  bentCVXFRX-f   
3  0xbb23c0361d3e436fb7942a0e103edecab3afa917  bentCVXFRX-f   
4  0xbb23c0361d3e436fb7942a0e103edecab3afa917  bentCVXFRX-f   

                            pool_coin_address pool_type  pool_metapool  \
0  0x9e0441e084f5db0606565737158aa6ab6b970fe0    CRYPTO          False   
1  0x3175df0976dfa876431c2e9ee6bc45b65d3473cc    CRYPTO          False   
2  0x9e0441e084f5db0606565737158aa6ab6b970fe0    CRYPTO          False   
3  0x3175df0976dfa876431c2e9ee6bc45b65d3473cc    CRYPTO          False   
4  0x9e0441e084f5db0606565737158aa6ab6b970fe0    CRYPTO          False   

  snapshot_timestamp  snapshot_tvl  snapshot_lp_price_usd  ...  \
0         2022-09-14      0.000000               0.000000  ...   
1         2022-09-14      0.000000               0.000000  ...   
2         2022-09-15    169.987405               2.280606  ...   
3         2022-09-15    169.987405               2.280606  ...   
4         2022-09-16    169.987856               2.280612  ...   

  pool_paired_fraxbp  snapshot_lp_supply pool_gauge  pool_cvx_token  \
0               True            0.000000        NaN             NaN   
1               True            0.000000        NaN             NaN   
2               True           74.536082        NaN             NaN   
3               True           74.536082        NaN             NaN   
4               True           74.536082        NaN             NaN   

   has_gauge  snapshot_crvFRAX_supply snapshot_bp_lp_metapool  \
0      False             8.751684e+08                     0.0   
1      False             8.751684e+08                     0.0   
2      False             8.375577e+08              169.869313   
3      False             8.375577e+08              169.869313   
4      False             8.575653e+08              169.869313   

  snapshot_bp_lp_metapool_share  snapshot_bp_lp_all_metapools  \
0                           0.0                61246270.31856   
1                           0.0                61246270.31856   
2                           0.0               59097598.700279   
3                           0.0               59097598.700279   
4                           0.0               61423556.551505   

   snapshot_bp_lp_all_metapools_share  
0                                 0.0  
1                                 0.0  
2                            0.000003  
3                            0.000003  
4                            0.000003  

[5 rows x 24 columns]

In [63]:
df_tvl = (
    df_pool_snaps[
        (df_pool_snaps.pool_coin_name != 'crvFRAX') & (df_pool_snaps.pool_address.str.lower() != ADDRESS_FRAXBP_POOL)
    ]
    .groupby("pool_name", sort="snapshot_timestamp").last().reset_index()
    [['snapshot_reserves_usd', 'pool_type', 'pool_coin_name']]
)
df_tvl = df_tvl.merge(
    df_tvl.groupby('pool_type')['snapshot_reserves_usd'].sum().reset_index().rename(columns={'snapshot_reserves_usd': 'tvl_total'}), 
    how='left', on="pool_type", validate="m:1"
)
df_tvl['tvl_share'] = df_tvl.snapshot_reserves_usd / df_tvl.tvl_total


In [64]:
(
    alt.Chart(df_tvl)
    .mark_arc()
    .encode(
        theta="snapshot_reserves_usd:Q", 
        color=alt.Color("pool_coin_name:N", scale=alt.Scale(scheme="tableau20")), 
        facet=alt.Facet('pool_type:N', columns=3),
        tooltip=[
            alt.Tooltip("pool_coin_name:N", title="Token"), 
            alt.Tooltip("snapshot_reserves_usd:Q", format="$,d", title="TVL"),
            alt.Tooltip("tvl_share:Q", format=".1%", title="TVL Share")
        ] 
    )
    .resolve_scale(theta="independent")
)

/opt/miniconda3/envs/frax-bribes/lib/python3.10/site-packages/altair/utils/core.py:317: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for col_name, dtype in df.dtypes.iteritems():


alt.Chart(...)

#### Current Metapool Liquidity Segmented By Asset Type 

In [65]:
df_tvl_type = df_pool_snaps[
    (df_pool_snaps.pool_coin_name != 'crvFRAX') & (df_pool_snaps.pool_address.str.lower() != ADDRESS_FRAXBP_POOL)
].copy()
df_tvl_type.snapshot_reserves_usd = df_tvl_type.snapshot_reserves_usd.astype(np.float64)
df_tvl_type = (
    df_tvl_type
    .groupby(["pool_type", "snapshot_timestamp"], dropna=False)['snapshot_reserves_usd'].sum().reset_index()
    .rename(columns={'snapshot_reserves_usd': 'tvl_type'})
)
df_tvl_total = df_tvl_type.groupby("snapshot_timestamp")['tvl_type'].sum().reset_index().rename(columns={'tvl_type': 'tvl_total'})

In [66]:
# df_tvl_type.sort_values(['snapshot_timestamp', 'pool_type']).tail(1)

In [67]:
# df_tvl_total.tail(1)

In [68]:
(
    alt.Chart(df_tvl_type)
    .mark_area()
    .encode(
        x="snapshot_timestamp:T", 
        y="tvl_type:Q", 
        color="pool_type:N", 
        tooltip=["pool_type:N", alt.Tooltip("tvl_type:Q", format="$,d")]
    ) + 
    alt.Chart(df_tvl_total)
    .mark_line(color="green")
    .encode(
        x="snapshot_timestamp:T", 
        y="tvl_total:Q", 
        tooltip=[alt.Tooltip("tvl_total:Q", format="$,d")]
    )
)

/opt/miniconda3/envs/frax-bribes/lib/python3.10/site-packages/altair/utils/core.py:317: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for col_name, dtype in df.dtypes.iteritems():


alt.LayerChart(...)

### Snapshot Proposals 

Here, we get the snapshot proposals that correspond to votium votes. Each proposal contains the possible set of choices (liquidity pools that rewards can be directed to). 

In [69]:
proposal_attrs = [
    'id', 
    'title', 
    'choices', 
    'created', 
    'start', 
    'end', 
    'state', 
    'scores_total', 
    
]
proposals = await graphql_execute(
    '''
    query Proposals {
      proposals(
        first: 10000,
        where: {title_contains: "Gauge weight", space: "cvx.eth"},
        orderBy: "created",
        orderDirection: desc
      ) {
        <proposal_attrs>
      }
    }
    '''.replace('<proposal_attrs>', '\n'.join(proposal_attrs))
)

In [70]:
async def get_snapshot_proposals(): 
    """Get all snapshot proposals corresponding to convex gauge weight votes. 
    
    Within each gauge weight vote, holders of vlCVX collectively determine how convex should distribute it's 
    veCRV in subsequent curve gauge votes. 
    
    - Votes are pulled from the snapshot graphql endpoint. 
    """
    proposal_attrs = ['id', 'title', 'choices', 'start', 'end', 'state']
    proposals = await graphql_execute(
        '''
        query Proposals {
          proposals(
            first: 10000,
            where: {
                title_contains: "Gauge weight", space: "cvx.eth"
            },
            orderBy: "created",
            orderDirection: desc
          ) {
            <proposal_attrs>
          }
        }
        '''.replace('<proposal_attrs>', '\n'.join(proposal_attrs))
    )
    # Number of rounds here should match number of rounds on llama airforce 
    # https://llama.airforce/#/bribes/rounds/votium/cvx-crv/
    df_proposals = pd.DataFrame(proposals['proposals'])
    df_proposals = df_proposals.loc[~df_proposals.title.str.startswith("(TEST)")]
    df_proposals.start = pd.to_datetime(df_proposals.start, unit='s').dt.date
    df_proposals.end = pd.to_datetime(df_proposals.end, unit='s').dt.date 
    df_proposals = df_proposals.sort_values('start').reset_index(drop=True)
    # On votium, the proposal id is keccak256 hashed. So we need to perform this operation on the data pulled from snapshot 
    df_proposals['id_keccak256'] = df_proposals.id.apply(
        lambda _id: Web3.keccak(text=_id).hex() if not _id.startswith('0x') else Web3.keccak(hexstr=_id).hex()
    )
    # Validate that this query pulls in all data by ensuring that the number of votium voting rounds we get from this query 
    # matches the expected number of voting rounds, which we can compute using simple timedelta logic, the date of the 
    # first vote, and the current date. 
    dmin = pd.Timestamp('2021-09-16') # day of the first votium snapshot 
    assert pd.Timestamp(df_proposals.start.min()) == dmin
    df_proposals['start_diff'] = df_proposals.start.shift(1) - df_proposals.start
    assert (df_proposals.iloc[1:,].start_diff == pd.Timedelta('-14 days')).all()
    # Since a proposal happens every two weeks, and we know the date of the first proposal, we can compute the number of expected proposals on any given date. 
    num_proposals_expected = (
        int(np.ceil((pd.Timestamp(pd.Timestamp.now().date()) - dmin) / pd.Timedelta("14 days")))
    )
    df_proposals['proposal_id'] = df_proposals.id 
    df_proposals = df_proposals.rename(columns={
        'title': 'proposal_title', 
        'choices': 'proposal_choices', 
        'start': 'proposal_start', 
        'end': 'proposal_end', 
        'id_keccak256': 'proposal_id_keccak256'
    })
    df_proposals = df_proposals.sort_values('proposal_start').reset_index(drop=True).reset_index()
    df_proposals['proposal_round'] = df_proposals['index'] + 1 
    df_proposals = df_proposals.drop(columns=['index', 'start_diff', 'id', 'state']) 
    assert len(df_proposals) == num_proposals_expected
    return df_proposals 
    
    
async def get_snapshot_votes(proposal_ids, verbose=True): 
    """Get all votes for all convex gauge weight snapshot proposals. 
        
    - Votes are pulled from the snapshot graphql endpoint. 
    """
    votes = await graphql_execute(
        '''
            query Votes($page_size: Int!, $page_offset: Int!, $proposal_ids: [String]!) {
              votes (
                first: $page_size
                skip: $page_offset
                where: { proposal_in: $proposal_ids }
              ) {
                proposal { id }
                id
                voter
                created
                choice
                vp
                vp_by_strategy
                vp_state
              }
            }
        ''', 
        paginate=True, 
        variable_values={'proposal_ids': proposal_ids}
    )
    vote_records = []
    for v in votes: 
        for index, amount in v['choice'].items(): 
            # TODO: data validation step / what does vp_state on this entity mean? Sometimes it's pending but still seems to be counted in votes. 
            # assert v['vp_state'] == 'final'
            r = {
                **v, 
                'choice_index': int(index) - 1, 
                'amount': amount, 
                'is_votium': v['voter'].lower() == VOTIUM_VOTER
            }
            del r['choice'] 
            vote_records.append(r)
    df_votes = pd.DataFrame(vote_records)
    df_votes['proposal_id'] = df_votes.proposal.apply(lambda v: v['id']) 
    df_votes['vote_id'] = df_votes['id'] 
    # Different voters represent their choice amount in different ways. So we group by each unique combination of voter and proposal and normalize on a per vote level. 
    df_votes['proposal_voter_amount_total'] = df_votes.groupby(['proposal_id', 'voter'])['amount'].transform('sum')
    df_votes['choice_percent'] = df_votes.amount / df_votes.proposal_voter_amount_total * 100
    df_votes = df_votes.drop(columns=['proposal', 'id', 'vp_by_strategy', 'vp_state', 'proposal_voter_amount_total']) 
    df_votes = df_votes.rename(columns={'created': 'vote_created', 'vp': 'vote_power'})
    return df_votes

In [71]:
df_proposals = await get_snapshot_proposals()

In [72]:
print(f"Number of votium snapshot proposals: {len(df_proposals)}")
df_proposals.head()

Number of votium snapshot proposals: 32


proposal_title  \
0  Gauge Weight for Week of 16th Sep 2021   
1  Gauge Weight for Week of 30th Sep 2021   
2  Gauge Weight for Week of 14th Oct 2021   
3  Gauge Weight for Week of 28th Oct 2021   
4  Gauge Weight for Week of 11th Nov 2021   

                                    proposal_choices proposal_start  \
0  [compound, usdt, ypool, busd, susd, pax, ren, ...     2021-09-16   
1  [compound, usdt, ypool, busd, susd, pax, ren, ...     2021-09-30   
2  [compound, usdt, ypool, busd, susd, pax, ren, ...     2021-10-14   
3  [compound, usdt, ypool, busd, susd, pax, ren, ...     2021-10-28   
4  [compound, usdt, ypool, busd, susd, pax, ren, ...     2021-11-11   

  proposal_end                              proposal_id_keccak256  \
0   2021-09-21  0xc841db892a58168d21262eb8e2f97d651fb354896fa9...   
1   2021-10-05  0xe11de27c199ddee0966ed8b24e1ee34bd3363f0fe09f...   
2   2021-10-19  0x20b26be17c62c2d155f9f9a9a3dac7bc3fcaa4845322...   
3   2021-11-02  0xb439c625f9f4929f6b486f79d5ae6850971d179a0887...   
4   2021-11-16  0x77cebe9bd4bc9836f115774c7387839e77abe3dda613...   

                                      proposal_id  proposal_round  
0  QmUjELF3ABSV2f5xgQrJgEnZTPb86DAtT6gzoa8RfHUuAK               1  
1  QmTQBqsG7dW93xX8zBZnevMa1mbEmDHUx7QabAYyn6mFJi               2  
2  QmaS9vd1vJKQNBYX4KWQ3nppsTT3QSL3nkz5ZYSwEJk6hZ               3  
3  QmacSRTG62rnvAyBuNY3cVbCtBHGV8PuGRoL32Dm6MPy5y               4  
4  QmPSBg5aTPb82sZRqF9ouUQQ5CkbpRaJMdHYUMieN3dpqv               5

In [73]:
df_choices = df_proposals.explode('proposal_choices').reset_index().rename(columns={'proposal_choices': 'choice'})
df_choices['choice_index'] = df_choices.groupby('proposal_id').cumcount()
df_choices = df_choices[['choice', 'choice_index', 'proposal_round', 'proposal_title', 'proposal_id', 'proposal_id_keccak256']]
df_choices['choice'] = df_choices.choice.str.lower()
df_choices.tail()

choice  choice_index  proposal_round  \
3571          op-sbtc+wbtc (0x9f2f…)           151              32   
3572      op-dai+usdc+usdt (0x1337…)           152              32   
3573          op-frax+usdc (0x29a3…)           153              32   
3574  xdai-wxdai+usdc+usdt (0x7f90…)           154              32   
3575                  vefunder-vyper           155              32   

                              proposal_title  \
3571  Gauge Weight for Week of 24th Nov 2022   
3572  Gauge Weight for Week of 24th Nov 2022   
3573  Gauge Weight for Week of 24th Nov 2022   
3574  Gauge Weight for Week of 24th Nov 2022   
3575  Gauge Weight for Week of 24th Nov 2022   

                                            proposal_id  \
3571  0xa0caae625a208e163a779b4b8a81892a4d5cef6fdc94...   
3572  0xa0caae625a208e163a779b4b8a81892a4d5cef6fdc94...   
3573  0xa0caae625a208e163a779b4b8a81892a4d5cef6fdc94...   
3574  0xa0caae625a208e163a779b4b8a81892a4d5cef6fdc94...   
3575  0xa0caae625a208e163a779b4b8a81892a4d5cef6fdc94...   

                                  proposal_id_keccak256  
3571  0x6f7cd62ef7e959053f1ee0e4374a8362ec08b237128f...  
3572  0x6f7cd62ef7e959053f1ee0e4374a8362ec08b237128f...  
3573  0x6f7cd62ef7e959053f1ee0e4374a8362ec08b237128f...  
3574  0x6f7cd62ef7e959053f1ee0e4374a8362ec08b237128f...  
3575  0x6f7cd62ef7e959053f1ee0e4374a8362ec08b237128f...

In [74]:
gauge_data = requests.get('https://api.curve.fi/api/getAllGauges').json()
df_gauges = pd.DataFrame([
    {
        'gauge_name': d['name'].lower(), 
        'gauge_short_name': d['shortName'].lower(), 
        'gauge_address': d['swap_token']
    } 
    for _, d in gauge_data['data'].items() 
])
df_gauges.head()

gauge_name           gauge_short_name  \
0    ibbtc+sbtccrv (0x99ae…bf27)    ibbtc+sbtccrv (0x99ae…)   
1       ausdc+adai (0x6a27…1dca)       ausdc+adai (0x6a27…)   
2  sdvecrv-dao+crv (0x737b…097b)  sdvecrv-dao+crv (0x737b…)   
3    btcpx+sbtccrv (0x4e52…2530)    btcpx+sbtccrv (0x4e52…)   
4        pwrd+3crv (0x2de8…e1a5)        pwrd+3crv (0x2de8…)   

                                gauge_address  
0  0x99ae07e7ab61dcce4383a86d14f61c68cdccbf27  
1  0x6a274de3e2462c7614702474d64d376729831dca  
2  0x737bc004136f66ae3f8fd5a1199e81c18388097b  
3  0x4e52cfc80679f402d10f7766fa3f85351a7c2530  
4  0x2de8c952871317fb9f22c73bb66bf86a1eebe1a5

In [75]:
proposal_ids = [e.lower() for e in df_proposals.proposal_id.unique().tolist()]
df_votes = await get_snapshot_votes(proposal_ids)

In [76]:
df_votes.head()

voter  vote_created   vote_power  \
0  0xc16aBC70d9c6e869f00ecFF397e7652b1847C570    1669655645  2163.406172   
1  0xDa2451FadeEE72eb1c88327871205Aa0Ec05E994    1669655529  1982.751759   
2  0xDa2451FadeEE72eb1c88327871205Aa0Ec05E994    1669655529  1982.751759   
3  0x1b3a46DE3a5E349b07B5a8B391cb4F1708E70bcc    1669655527  1452.053591   
4  0x8C59c640D1428ba96Cdf597187d840dBD9e09dfB    1669655474  1559.447539   

   choice_index amount  is_votium  \
0            68    100      False   
1            56      1      False   
2            68      1      False   
3           120      1      False   
4            38      1      False   

                                         proposal_id  \
0  0xa0caae625a208e163a779b4b8a81892a4d5cef6fdc94...   
1  0xa0caae625a208e163a779b4b8a81892a4d5cef6fdc94...   
2  0xa0caae625a208e163a779b4b8a81892a4d5cef6fdc94...   
3  0xa0caae625a208e163a779b4b8a81892a4d5cef6fdc94...   
4  0xa0caae625a208e163a779b4b8a81892a4d5cef6fdc94...   

                                             vote_id choice_percent  
0  0x5103259b4aa7a17fb3bf4e2b5794cb3224d33fba4701...          100.0  
1  0xfafb582dd3638417b12210d60b96167f03b7b79b9970...           50.0  
2  0xfafb582dd3638417b12210d60b96167f03b7b79b9970...           50.0  
3  0x6ec60f2159cfd647a1f444a00d5b7fcdba00709a8d6f...          100.0  
4  0x0f5f68a29049f9493263f3a1cb367070d15ce7788f3b...           50.0

In [77]:
df_snaps = df_votes.merge(df_proposals, how='left', on='proposal_id', validate='m:1')

def row_mapper(row): 
    row['vote_choice'] = row['proposal_choices'][int(row['choice_index'])]
    return row 

df_snaps = df_snaps.apply(row_mapper, axis=1)
df_snaps['vote_power_allocated'] = (df_snaps.choice_percent / 100) * df_snaps.vote_power 
df_snaps = df_snaps[[
    'proposal_round', 'proposal_title', 'proposal_start', 'proposal_end', 'voter', 'vote_power', 
    'vote_created', 'vote_choice', 'choice_percent', 'choice_index', 
    'vote_power_allocated', 
    'proposal_id', 'vote_id', 'proposal_id_keccak256'
]]
df_snaps = df_snaps.sort_values(['proposal_round', 'proposal_start']).reset_index(drop=True) 
# df_snaps.choice_index = df_snaps.choice_index.astype(int)

In [78]:
(
    alt.Chart((
        df_snaps[['proposal_round', 'vote_choice', 'vote_power_allocated']]
        .groupby(['proposal_round', 'vote_choice']).sum()
        .reset_index() 
    ))
    .mark_bar()
    .encode(
        x="proposal_round:O", 
        y="vote_power_allocated:Q", 
        color="vote_choice:N", 
        tooltip=["vote_choice:N", "vote_power_allocated:Q"]
    )
    .properties(width=500) 
)

/opt/miniconda3/envs/frax-bribes/lib/python3.10/site-packages/altair/utils/core.py:317: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for col_name, dtype in df.dtypes.iteritems():


alt.Chart(...)

### Votium Bribes 

In [79]:
df_snaps.head()

proposal_round                          proposal_title proposal_start  \
0               1  Gauge Weight for Week of 16th Sep 2021     2021-09-16   
1               1  Gauge Weight for Week of 16th Sep 2021     2021-09-16   
2               1  Gauge Weight for Week of 16th Sep 2021     2021-09-16   
3               1  Gauge Weight for Week of 16th Sep 2021     2021-09-16   
4               1  Gauge Weight for Week of 16th Sep 2021     2021-09-16   

  proposal_end                                       voter    vote_power  \
0   2021-09-21  0xde1E6A7ED0ad3F61D531a8a78E83CcDdbd6E0c49  2.171453e+06   
1   2021-09-21  0xde1E6A7ED0ad3F61D531a8a78E83CcDdbd6E0c49  2.171453e+06   
2   2021-09-21  0xde1E6A7ED0ad3F61D531a8a78E83CcDdbd6E0c49  2.171453e+06   
3   2021-09-21  0xde1E6A7ED0ad3F61D531a8a78E83CcDdbd6E0c49  2.171453e+06   
4   2021-09-21  0xde1E6A7ED0ad3F61D531a8a78E83CcDdbd6E0c49  2.171453e+06   

   vote_created vote_choice  choice_percent  choice_index  \
0    1632182562        eurs        8.720190            22   
1    1632182562     ankreth       10.245874            27   
2    1632182562        frax       63.664015            32   
3    1632182562       alusd       17.308531            36   
4    1632182562      cvxcrv        0.061390            41   

   vote_power_allocated                                     proposal_id  \
0          1.893549e+05  QmUjELF3ABSV2f5xgQrJgEnZTPb86DAtT6gzoa8RfHUuAK   
1          2.224844e+05  QmUjELF3ABSV2f5xgQrJgEnZTPb86DAtT6gzoa8RfHUuAK   
2          1.382434e+06  QmUjELF3ABSV2f5xgQrJgEnZTPb86DAtT6gzoa8RfHUuAK   
3          3.758467e+05  QmUjELF3ABSV2f5xgQrJgEnZTPb86DAtT6gzoa8RfHUuAK   
4          1.333058e+03  QmUjELF3ABSV2f5xgQrJgEnZTPb86DAtT6gzoa8RfHUuAK   

                                          vote_id  \
0  QmZ6KsSz71Q93VY9RXjbKXUPX36VBAhFJqe8wX6jJuEaBa   
1  QmZ6KsSz71Q93VY9RXjbKXUPX36VBAhFJqe8wX6jJuEaBa   
2  QmZ6KsSz71Q93VY9RXjbKXUPX36VBAhFJqe8wX6jJuEaBa   
3  QmZ6KsSz71Q93VY9RXjbKXUPX36VBAhFJqe8wX6jJuEaBa   
4  QmZ6KsSz71Q93VY9RXjbKXUPX36VBAhFJqe8wX6jJuEaBa   

                               proposal_id_keccak256  
0  0xc841db892a58168d21262eb8e2f97d651fb354896fa9...  
1  0xc841db892a58168d21262eb8e2f97d651fb354896fa9...  
2  0xc841db892a58168d21262eb8e2f97d651fb354896fa9...  
3  0xc841db892a58168d21262eb8e2f97d651fb354896fa9...  
4  0xc841db892a58168d21262eb8e2f97d651fb354896fa9...

In [80]:
# Get all votium voting epochs. Once we have validated that this set of epochs matches our set of snapshot proposals, 
# we need to merge this data with our snapshot proposal data. 
epoches = sg_votium.Query.epoches(first=1000, orderBy="initiatedAt", where={"bribeCount_gt": 0})
df_epoches = sg.query_df([epoches.id, epoches.initiatedAt], pagination_strategy=ShallowStrategy)
# df_epoches = remove_prefix(df_epoches, "epoches_")
df_epoches.epoches_initiatedAt = pd.to_datetime(df_epoches.epoches_initiatedAt, unit="s")
df_epoches['date'] = df_epoches.epoches_initiatedAt.dt.date
# Validate that the epoch dates for votium bribes match the proposal data we pulled from snapshot. `
epoch_dates = df_epoches.date.unique().tolist()
proposal_dates = df_snaps.proposal_start.unique().tolist()
d_exclude = pd.Timestamp('2021-11-08').date()
assert d_exclude in epoch_dates and not d_exclude in proposal_dates
epoch_dates.remove(d_exclude)
assert set(epoch_dates) == set(proposal_dates)
df_epoches = df_epoches.loc[df_epoches.date != d_exclude].reset_index(drop=True)
df_epoches = df_epoches.sort_values('date').reset_index().rename(columns={'index': 'round'})
df_epoches['round'] += 1
df_epoches.tail()

round                                         epoches_id  \
27     28  0x0f5d75e0b0b506ba9ff2c394d40ed7b105e9a3523d53...   
28     29  0xb9262aa45b24da69f1793438d6f43da0425d99ae2e72...   
29     30  0xf25f333d0eff881950706755ca73764e3875f76d5012...   
30     31  0xc7e65a46a6fa9a085ff994c30ba19c95cbaf8ee64c49...   
31     32  0x6f7cd62ef7e959053f1ee0e4374a8362ec08b237128f...   

   epoches_initiatedAt        date  
27 2022-09-29 00:00:59  2022-09-29  
28 2022-10-13 00:01:23  2022-10-13  
29 2022-10-27 00:03:11  2022-10-27  
30 2022-11-10 00:01:35  2022-11-10  
31 2022-11-24 00:00:35  2022-11-24

In [81]:
# https://github.com/convex-community/convex-subgraph/blob/main/subgraphs/votium/src/mapping.ts

# Addresses associated with the frax protocol used for votium bribes 
# TODO: Frax controls some subset of the TVL in it's liquidity pools. Need to be cognizant of this because it leads 
#       to a rebate the lowers the cost of bribing. 
# TODO: Frax's vlCVX is not custodied in the investor custodian wallet. 
frax_bribe_addresses = [
    # ('comptroller', '0xb1748c79709f4ba2dd82834b8c82d4a505003f27'),
    # ('cvx locker amo', '0x7038c406e7e2c9f81571557190d26704bb39b8f3'),
    ('investor custodian', '0x5180db0237291A6449DdA9ed33aD90a38787621c'),
    ('frax1.eth', '0x234D953a9404Bf9DbC3b526271d440cD2870bCd2'),
]
# TODO: Check to see if there are bribes in FRAX 
bribes = sg_votium.Query.bribes(first=100000, where={
    "epoch_in": df_epoches.epoches_id.unique().tolist(), "token": ADDRESS_FXS
})
df_bribes = sg.query_df([bribes.id, bribes.amount, bribes.choiceIndex, bribes.epoch.id], pagination_strategy=ShallowStrategy)
df_bribes = remove_prefix(df_bribes, "bribes_")
df_bribes['tx_hash'] = df_bribes['id'].apply(lambda _id: _id.split('-')[0])
df_bribes.amount /= 1e18
df_bribes = df_bribes.drop(columns=['id'])
df_bribes = df_bribes.rename(columns={'amount': 'bribe_fxs', 'choiceIndex': 'choice_index'})
ddf(df_bribes.head())

In [82]:
# Determine the "from" address for the transaction that contained the bribe 
tx_hashes = df_bribes.tx_hash.unique()

def get_tx(tx_hash): 
    return w3.eth.get_transaction(tx_hash)['from'] 

tx_from_map = {}
with concurrent.futures.ThreadPoolExecutor(max_workers=10) as executor:
    futures = {tx_hash: executor.submit(get_tx, tx_hash) for tx_hash in tx_hashes}
    for tx_hash, future in futures.items(): 
        tx_from_map[tx_hash] = future.result()

In [83]:
df_bribes['from'] = df_bribes['tx_hash'].apply(lambda tx_hash: tx_from_map[tx_hash])
address_labels = {addr.lower(): name for name, addr in frax_bribe_addresses}
df_bribes['briber_label'] = df_bribes['from'].apply(lambda a: address_labels.get(a.lower()))
label_counts = df_bribes.briber_label.value_counts(dropna=False)
print("Label count for bribing address") 
print(label_counts)
print(f"Dropping {label_counts[None]} bribe(s)")
df_bribes = df_bribes.loc[~df_bribes.briber_label.isna()] 
df_bribes = df_bribes.drop(columns=['tx_hash', 'from']).sort_values(['briber_label', 'choice_index']).reset_index(drop=True)
df_bribes.head()

Label count for bribing address
investor custodian    159
frax1.eth              21
None                    1
Name: briber_label, dtype: int64
Dropping 1 bribe(s)


bribe_fxs  choice_index                                           epoch_id  \
0   31509.12            32  0xe11de27c199ddee0966ed8b24e1ee34bd3363f0fe09f...   
1   76922.88            32  0x20b26be17c62c2d155f9f9a9a3dac7bc3fcaa4845322...   
2   37280.64            32  0xc841db892a58168d21262eb8e2f97d651fb354896fa9...   
3  147040.32            33  0xc26deaa05f45f3f6ad088cb6603d77cb2e826ff98b69...   
4  219089.28            33  0xee224d8e52bc9240eef248d30fa4b1a525c0f686da23...   

  briber_label  
0    frax1.eth  
1    frax1.eth  
2    frax1.eth  
3    frax1.eth  
4    frax1.eth

In [84]:
# Match bribes with their corresponding round 
df_bribes_full = df_epoches.merge(df_bribes, how='right', left_on='epoches_id', right_on='epoch_id', validate='1:m') 
df_bribes_full.head()

round                                         epoches_id  \
0      2  0xe11de27c199ddee0966ed8b24e1ee34bd3363f0fe09f...   
1      3  0x20b26be17c62c2d155f9f9a9a3dac7bc3fcaa4845322...   
2      1  0xc841db892a58168d21262eb8e2f97d651fb354896fa9...   
3      7  0xc26deaa05f45f3f6ad088cb6603d77cb2e826ff98b69...   
4      8  0xee224d8e52bc9240eef248d30fa4b1a525c0f686da23...   

  epoches_initiatedAt        date  bribe_fxs  choice_index  \
0 2021-09-30 00:02:12  2021-09-30   31509.12            32   
1 2021-10-14 00:04:43  2021-10-14   76922.88            32   
2 2021-09-16 00:04:43  2021-09-16   37280.64            32   
3 2021-12-09 00:10:50  2021-12-09  147040.32            33   
4 2021-12-23 00:02:44  2021-12-23  219089.28            33   

                                            epoch_id briber_label  
0  0xe11de27c199ddee0966ed8b24e1ee34bd3363f0fe09f...    frax1.eth  
1  0x20b26be17c62c2d155f9f9a9a3dac7bc3fcaa4845322...    frax1.eth  
2  0xc841db892a58168d21262eb8e2f97d651fb354896fa9...    frax1.eth  
3  0xc26deaa05f45f3f6ad088cb6603d77cb2e826ff98b69...    frax1.eth  
4  0xee224d8e52bc9240eef248d30fa4b1a525c0f686da23...    frax1.eth

In [85]:
df_choices.head()

choice  choice_index  proposal_round  \
0  compound             0               1   
1      usdt             1               1   
2     ypool             2               1   
3      busd             3               1   
4      susd             4               1   

                           proposal_title  \
0  Gauge Weight for Week of 16th Sep 2021   
1  Gauge Weight for Week of 16th Sep 2021   
2  Gauge Weight for Week of 16th Sep 2021   
3  Gauge Weight for Week of 16th Sep 2021   
4  Gauge Weight for Week of 16th Sep 2021   

                                      proposal_id  \
0  QmUjELF3ABSV2f5xgQrJgEnZTPb86DAtT6gzoa8RfHUuAK   
1  QmUjELF3ABSV2f5xgQrJgEnZTPb86DAtT6gzoa8RfHUuAK   
2  QmUjELF3ABSV2f5xgQrJgEnZTPb86DAtT6gzoa8RfHUuAK   
3  QmUjELF3ABSV2f5xgQrJgEnZTPb86DAtT6gzoa8RfHUuAK   
4  QmUjELF3ABSV2f5xgQrJgEnZTPb86DAtT6gzoa8RfHUuAK   

                               proposal_id_keccak256  
0  0xc841db892a58168d21262eb8e2f97d651fb354896fa9...  
1  0xc841db892a58168d21262eb8e2f97d651fb354896fa9...  
2  0xc841db892a58168d21262eb8e2f97d651fb354896fa9...  
3  0xc841db892a58168d21262eb8e2f97d651fb354896fa9...  
4  0xc841db892a58168d21262eb8e2f97d651fb354896fa9...

In [86]:
df = (
    df_bribes_full.groupby(['round', 'choice_index'])['bribe_fxs'].sum()
    .reset_index()
    .merge(
        df_choices[['proposal_round', 'choice', 'choice_index']], 
        how='left',
        left_on=['round', 'choice_index'],
        right_on=['proposal_round', 'choice_index'], validate='m:1'
    )
    .merge(
        df_epoches[['round', 'epoches_initiatedAt']], 
        how='left', 
        on='round', 
        validate='m:1'
    )
    .drop(columns=['round'])
    .rename(columns={'epoches_initiatedAt': 'epoch_initiated_at'})
)
df['timestamp'] = pd.to_datetime(pd.to_datetime((df.epoch_initiated_at.astype(int) / 1e9).astype(int), unit='s').dt.date)
df.choice = df.choice.str.lower()
df.head()

choice_index  bribe_fxs  proposal_round choice  epoch_initiated_at  \
0            32   37280.64               1   frax 2021-09-16 00:04:43   
1            32   31509.12               2   frax 2021-09-30 00:02:12   
2            32   76922.88               3   frax 2021-10-14 00:04:43   
3            33   72288.96               4   frax 2021-10-28 11:02:59   
4            33  116033.28               5   frax 2021-11-11 00:04:34   

   timestamp  
0 2021-09-16  
1 2021-09-30  
2 2021-10-14  
3 2021-10-28  
4 2021-11-11

In [87]:
def process(df): 
    # Goal: For each choice in the snapshot proposal (i.e. a curve pool gauge), we want to pair the 
    #       choice name taken from the snapshot API with the address of the curve pool that choice 
    #       corresponds to. 
    
    # Remove irrelevant gauges  
    remove_choices = [
        "arbitrum-f-4pool", # 4pool never launched 
        "tusd", # Only bribed for in 1 round. Not really sure what to do about this one 
    ]
    df = df.loc[~df.choice.isin(remove_choices)]
    
    def preprocess_choice(choice):
        # Some older voting rounds used crvfrax while newer ones use fraxbp 
        choice = choice.replace('crvfrax', 'fraxbp')
        # Some older voting rounds prefixed factory pools with f- while newer rounds do not
        if choice.startswith("f-"): 
            choice = choice[2:]
        # Some older voting rounds showed addresses in form (0x...ab123)
        # whereas newer rounds use the form (0x...) without trailing values. 
        # Here, we remove trailing values if they exist 
        m = re.search('.*\\u2026([^\)]*)\)$', choice)
        if m: 
            choice = choice.replace(m.group(1), '') 
        return choice 
        
    df.choice = df.choice.apply(preprocess_choice)
    
    # We get the current set of gauges from the curve API. These names are what appear in the snapshot proposal 
    # This will get the most recent set of names but the structure of the names has changed over time. More work 
    # needs to be done to account for historical differences in naming pools 
    df = df.merge(df_gauges, how='left', left_on='choice', right_on='gauge_short_name')
    
    missed = df.loc[df.gauge_name.isna()].choice.unique()
 
    df_canonical_choices = pd.DataFrame(
        columns=['choice', 'canonical_choice'], 
        data=[
            ['frax', 'frax+usdc (0xdcef…)'], # fraxbp 
            ['d3pool', 'frax+fei+alusd (0xbaaa…)'], 
            ['fpifrax', 'frax+fpi (0xf861…)'], 
            ['2pool-frax', 'frax+usdc (0xdcef…)'], # fraxbp 
            ['fraxbpsusd', 'susd+fraxbp (0xe3c1…)'], 
            ['fraxbplusd', 'lusd+fraxbp (0x497c…)'], 
            ['fraxbpbusd', 'busd+fraxbp (0x8fdb…)'], 
            ['fraxbpape', 'apeusd+fraxbp (0x04b7…)'], 
            ['fraxbpalusd', 'alusd+fraxbp (0xb30d…)'], 
            ['fraxbpusdd', 'usdd+fraxbp (0x4606…)'], 
            ['fraxbptusd', 'tusd+fraxbp (0x33ba…)'], 
            ['fraxbpgusd', 'gusd+fraxbp (0x4e43…)'], 
        ]
    )    
    copy_cols = ['gauge_name', 'gauge_short_name', 'gauge_address']
    df = df.merge(df_canonical_choices, how='left', on='choice', validate='m:1')
    assert set(df.canonical_choice.dropna().unique()) == set(df_canonical_choices.canonical_choice.unique())
    df = pd.concat([
        # subset where we have already matched a choice to a gauge 
        df.loc[~df.gauge_name.isna()], 
        # subset where we have NOT matched a choice to a gauge 
        (
            df.loc[df.gauge_name.isna()]
            .drop(columns=df_gauges.columns.values.tolist()) 
            .merge(df_gauges, how='left', left_on='canonical_choice', right_on='gauge_short_name')
        )
    ])
    
    assert all(~df.gauge_address.isna()), "Unable to identify lp address for some choices"

    df = df.sort_values(['proposal_round', 'choice']).reset_index(drop=True)

    # miss.matrix(df)
    return df 

df = process(df) 

<>:22: DeprecationWarning: invalid escape sequence '\)'
<>:22: DeprecationWarning: invalid escape sequence '\)'
/var/folders/5c/hf9_blgj3jbbxxvkw_s9snsw0000gn/T/ipykernel_53637/1384607546.py:22: DeprecationWarning: invalid escape sequence '\)'
  m = re.search('.*\\u2026([^\)]*)\)$', choice)
/var/folders/5c/hf9_blgj3jbbxxvkw_s9snsw0000gn/T/ipykernel_53637/1384607546.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.choice = df.choice.apply(preprocess_choice)


In [88]:
print(len(df.gauge_short_name.unique()))

24


In [89]:
# var = 'choice' 
var = 'gauge_short_name'
# var = 'gauge_address' 
(
    alt.Chart(df)
    .mark_bar()
    .encode(
        x="proposal_round:O", 
        y="bribe_fxs:Q", 
        color=f"{var}:N", 
        tooltip=[f'{var}:N', 'bribe_fxs:Q']
    )
)

/opt/miniconda3/envs/frax-bribes/lib/python3.10/site-packages/altair/utils/core.py:317: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for col_name, dtype in df.dtypes.iteritems():


alt.Chart(...)

In [90]:
df = df[['proposal_round', 'timestamp', 'gauge_short_name', 'bribe_fxs', 'gauge_address']] 
df.head()

# miss.matrix(df)

proposal_round  timestamp          gauge_short_name bribe_fxs  \
0               1 2021-09-16       frax+usdc (0xdcef…)  37280.64   
1               2 2021-09-30       frax+usdc (0xdcef…)  31509.12   
2               3 2021-10-14       frax+usdc (0xdcef…)  76922.88   
3               4 2021-10-28       frax+usdc (0xdcef…)  72288.96   
4               5 2021-11-11  frax+fei+alusd (0xbaaa…)   2368.32   

                                gauge_address  
0  0x3175df0976dfa876431c2e9ee6bc45b65d3473cc  
1  0x3175df0976dfa876431c2e9ee6bc45b65d3473cc  
2  0x3175df0976dfa876431c2e9ee6bc45b65d3473cc  
3  0x3175df0976dfa876431c2e9ee6bc45b65d3473cc  
4  0xbaaa1f5dba42c3389bdbc2c9d2de134f5cd0dc89

In [91]:
df_liquidity.dailyPoolSnapshots_timestamp = pd.to_datetime(df_liquidity.dailyPoolSnapshots_timestamp, unit='s')
df_liquidity = df_liquidity[
    ['dailyPoolSnapshots_timestamp', 'dailyPoolSnapshots_reservesUSD', 'pool_address', 'pools_name', 'pools_lpToken', 'pools_coins', 'pools_coinNames']
]
df_liquidity.head()

NameError: name 'df_liquidity' is not defined

In [ ]:
# Map each bribe to liquidty data point for it's corresponding pool 
dff_join = pd.merge_asof(
    df.sort_values('timestamp').reset_index(drop=True),
    df_liquidity.sort_values('dailyPoolSnapshots_timestamp').reset_index(drop=True),
    left_by=['gauge_address'], 
    right_by=['pool_address'], 
    left_on=['timestamp'], 
    right_on=['dailyPoolSnapshots_timestamp', ], 
)[['proposal_round', 'dailyPoolSnapshots_timestamp', 'gauge_short_name', 'bribe_fxs', 'gauge_address']]
dff_join = dff_join.loc[~dff_join.dailyPoolSnapshots_timestamp.isna()]
print(len(dff_join))
dff_join.head()

In [ ]:
df_liquidity.head()

In [ ]:
dff_join.head()

In [ ]:
dff = (
    # 1. Ensure that the gauge information is attached to liquidity data 
    df_liquidity
    .merge(
        dff_join[['gauge_short_name', 'gauge_address']].drop_duplicates().reset_index(drop=True), 
        how='left', 
        left_on='pool_address', 
        right_on='gauge_address'
    ) 
    .merge(
        dff_join[['gauge_address', 'bribe_fxs', 'proposal_round', 'dailyPoolSnapshots_timestamp']], 
        how='left', 
        left_on=['pool_address', 'dailyPoolSnapshots_timestamp'], 
        right_on=['gauge_address', 'dailyPoolSnapshots_timestamp'], 
    ) 
    .drop(columns=['gauge_address_y'])
) 
dff = dff.loc[~dff.gauge_short_name.isna()]

# dff.bribe_fxs = dff.bribe_fxs.fillna(0)
# miss.matrix(dff) 
print(len(df_liquidity))
print(len(dff))

dff.head()

In [ ]:
# base = (
#     alt.Chart(dff)
#     .transform_calculate(stack_order="datum.pools_coinNames === 'crvFRAX' ? 0 : 1")
#     .encode(
        
#         color=alt.Color("pools_coinNames:N", scale=alt.Scale(scheme="tableau20")), 
#         tooltip=alt.Tooltip("dailyPoolSnapshots_reservesUSD:Q", format='$,d'), 
#         facet=alt.Facet('pools_symbol:N', columns=3),
#         order="stack_order:O", 
#     )
#     .resolve_scale(y="independent")
# )
# liquidity = (
#     base
#     .mark_area()
#     .encode(
#         x="dailyPoolSnapshots_timestamp:T", 
#         y="dailyPoolSnapshots_reservesUSD:Q"
#     )
#     # .resolve_scale(y="independent")
# )
# bribes = (
#     base
#     .mark_bar()
#     .encode(
#         x="dailyPoolSnapshots_timestamp:T", 
#         y="bribe_fxs:Q",
#     )
#     .resolve_scale(y="independent")
# )

# # miss.matrix(dff)

# liquidity | bribes 

In [ ]:
miss.matrix(dff)

In [ ]:
dff.head()

In [ ]:
max_bribe

In [ ]:
ncols = 3 
rows = []
row = []
gnames = dff.gauge_short_name.unique().tolist()

max_tvl = (
    dff.groupby(['dailyPoolSnapshots_timestamp', 'gauge_short_name'])['dailyPoolSnapshots_reservesUSD'].sum().max()
)
max_bribe = (
    dff['bribe_fxs'].max() 
)

while gnames: 
    gname = gnames.pop()
    # add data for this gauge to current row 
    sdf = dff.loc[dff.gauge_short_name == gname] 
    base = (
        alt.Chart(sdf)
        .transform_calculate(stack_order="datum.pools_coinNames === 'crvFRAX' ? 0 : 1")
        .encode(
            x="dailyPoolSnapshots_timestamp:T", 
            color=alt.Color("pools_coinNames:N", scale=alt.Scale(scheme="tableau20")), 
            order="stack_order:O", 
        )
        .properties(width=250, height=150) 
    )
    liquidity = base.mark_area().encode(
        y=alt.Y("dailyPoolSnapshots_reservesUSD:Q", scale=alt.Scale(domain=[0, max_tvl * 1.05])),
        tooltip=alt.Tooltip("dailyPoolSnapshots_reservesUSD:Q", format='$,d'), 
    )
    bribes = (
        base
        .transform_filter("datum.pools_coinNames === 'crvFRAX'")
        .mark_bar()
        .encode(
            y=alt.Y("bribe_fxs:Q", scale=alt.Scale(domain=[0, max_bribe * 1.05])),
            tooltip=alt.Tooltip("bribe_fxs:Q", format=',d'), 
        )
    )
    row.append(alt.vconcat(liquidity, bribes).resolve_scale(x="shared").resolve_axis(x='shared'))
    if len(row) == ncols: 
        rows.append(row) 
        row = []
    
rows = [alt.hconcat(*row) for row in rows]
chart = alt.vconcat(*rows)    
chart


In [ ]:
sdf[~sdf.bribe_fxs.isna()].head()

# miss.matrix(sdf)
# ddf(df_liquidity.loc[df_liquidity.pools_coinNames == 'ApeUSD'].head(20))